In [1]:
import requests
import pandas as pd
import sqlite3
import json
import sqlalchemy
from sqlalchemy import create_engine, select, MetaData, table, and_
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy.orm import Session
from sqlalchemy.ext.automap import automap_base
from sqlalchemy.inspection import inspect

In [2]:
# Code that gives us the first 10 rows from the API
# payload = {'$limit':25} # Token: QKIJJkCC1jXBt8cZgtpgWRinW
r = requests.get('https://data.cityofnewyork.us/resource/erm2-nwe9.json')

In [3]:
r.json()

[{'unique_key': '53699338',
  'created_date': '2022-03-21T01:59:35.000',
  'agency': 'NYPD',
  'agency_name': 'New York City Police Department',
  'complaint_type': 'Blocked Driveway',
  'descriptor': 'No Access',
  'location_type': 'Street/Sidewalk',
  'incident_zip': '11207',
  'incident_address': '2869 FULTON STREET',
  'street_name': 'FULTON STREET',
  'cross_street_1': 'BARBEY STREET',
  'cross_street_2': 'JEROME STREET',
  'intersection_street_1': 'BARBEY STREET',
  'intersection_street_2': 'JEROME STREET',
  'address_type': 'ADDRESS',
  'city': 'BROOKLYN',
  'landmark': 'FULTON STREET',
  'status': 'In Progress',
  'community_board': '05 BROOKLYN',
  'bbl': '3039360042',
  'borough': 'BROOKLYN',
  'x_coordinate_state_plane': '1015115',
  'y_coordinate_state_plane': '186549',
  'open_data_channel_type': 'MOBILE',
  'park_facility_name': 'Unspecified',
  'park_borough': 'BROOKLYN',
  'latitude': '40.67865686334285',
  'longitude': '-73.88872245329644',
  'location': {'latitude': '

In [4]:
connector = sqlite3.connect('calls.db') # sqlite3 will create db if does not exist

In [5]:
cursor = connector.cursor()

In [6]:
create_raw_json_table = """ CREATE TABLE raw_json(
                            id INTEGER PRIMARY KEY AUTOINCREMENT,
                            raw_text text
                        )"""

In [7]:
cursor.execute(create_raw_json_table) # Creating table

In [8]:
connector.commit() # Comitting changes

In [9]:
# json.loads(), json.dumps()
lst = [(json.dumps(row),) for row in r.json()] # json.dumps() converts some json into str, json.loads() takes str and converts it back to json
lst

[('{"unique_key": "53699338", "created_date": "2022-03-21T01:59:35.000", "agency": "NYPD", "agency_name": "New York City Police Department", "complaint_type": "Blocked Driveway", "descriptor": "No Access", "location_type": "Street/Sidewalk", "incident_zip": "11207", "incident_address": "2869 FULTON STREET", "street_name": "FULTON STREET", "cross_street_1": "BARBEY STREET", "cross_street_2": "JEROME STREET", "intersection_street_1": "BARBEY STREET", "intersection_street_2": "JEROME STREET", "address_type": "ADDRESS", "city": "BROOKLYN", "landmark": "FULTON STREET", "status": "In Progress", "community_board": "05 BROOKLYN", "bbl": "3039360042", "borough": "BROOKLYN", "x_coordinate_state_plane": "1015115", "y_coordinate_state_plane": "186549", "open_data_channel_type": "MOBILE", "park_facility_name": "Unspecified", "park_borough": "BROOKLYN", "latitude": "40.67865686334285", "longitude": "-73.88872245329644", "location": {"latitude": "40.67865686334285", "longitude": "-73.88872245329644",

In [10]:
cursor.executemany("INSERT INTO raw_json (raw_text) VALUES (?)", lst)
connector.commit()
connector.close()

In [11]:
connector = sqlite3.connect('calls.db')
cursor = connector.cursor()

In [12]:
cursor.execute('select * from raw_json')
x = cursor.fetchall()
for row in x:
    print(row, '\n')
connector.close()

(1, '{"unique_key": "53699338", "created_date": "2022-03-21T01:59:35.000", "agency": "NYPD", "agency_name": "New York City Police Department", "complaint_type": "Blocked Driveway", "descriptor": "No Access", "location_type": "Street/Sidewalk", "incident_zip": "11207", "incident_address": "2869 FULTON STREET", "street_name": "FULTON STREET", "cross_street_1": "BARBEY STREET", "cross_street_2": "JEROME STREET", "intersection_street_1": "BARBEY STREET", "intersection_street_2": "JEROME STREET", "address_type": "ADDRESS", "city": "BROOKLYN", "landmark": "FULTON STREET", "status": "In Progress", "community_board": "05 BROOKLYN", "bbl": "3039360042", "borough": "BROOKLYN", "x_coordinate_state_plane": "1015115", "y_coordinate_state_plane": "186549", "open_data_channel_type": "MOBILE", "park_facility_name": "Unspecified", "park_borough": "BROOKLYN", "latitude": "40.67865686334285", "longitude": "-73.88872245329644", "location": {"latitude": "40.67865686334285", "longitude": "-73.88872245329644

In [13]:
# Helper function to get raw data

def get_raw():
    connector = sqlite3.connect('calls.db')
    cursor = connector.cursor()
    lst = [row for row in cursor.execute('SELECT * from raw_json')]
    connector.close()
    return lst

In [14]:
raw = get_raw()

In [15]:
# Takes in list of tuples
# Prune features we don't need

def data_extractor(lst):
        kvs = ['created_date','agency','agency_name',
            'complaint_type','descriptor', 'location_type',
            'incident_zip','incident_address','borough', ]
        info = []
        for x, y in lst:
                temp = {}
                parsed_json = json.loads(y)
                for k, v in parsed_json.items():
                        if k in kvs:
                                temp[k] = v
                info.append(temp)
        return info

In [16]:
data_extractor(raw)

[{'created_date': '2022-03-21T01:59:35.000',
  'agency': 'NYPD',
  'agency_name': 'New York City Police Department',
  'complaint_type': 'Blocked Driveway',
  'descriptor': 'No Access',
  'location_type': 'Street/Sidewalk',
  'incident_zip': '11207',
  'incident_address': '2869 FULTON STREET',
  'borough': 'BROOKLYN'},
 {'created_date': '2022-03-21T01:59:35.000',
  'agency': 'NYPD',
  'agency_name': 'New York City Police Department',
  'complaint_type': 'Blocked Driveway',
  'descriptor': 'No Access',
  'location_type': 'Street/Sidewalk',
  'incident_zip': '11207',
  'incident_address': '2869 FULTON STREET',
  'borough': 'BROOKLYN'},
 {'created_date': '2022-03-21T01:59:05.000',
  'agency': 'NYPD',
  'agency_name': 'New York City Police Department',
  'complaint_type': 'Noise - Vehicle',
  'descriptor': 'Engine Idling',
  'location_type': 'Street/Sidewalk',
  'incident_zip': '11373',
  'incident_address': '92-01 51 AVENUE',
  'borough': 'QUEENS'},
 {'created_date': '2022-03-21T01:58:34.

In [17]:
df = pd.DataFrame(data_extractor(raw))
df

created_date agency                              agency_name  \
0    2022-03-21T01:59:35.000   NYPD          New York City Police Department   
1    2022-03-21T01:59:35.000   NYPD          New York City Police Department   
2    2022-03-21T01:59:05.000   NYPD          New York City Police Department   
3    2022-03-21T01:58:34.000   NYPD          New York City Police Department   
4    2022-03-21T01:57:09.000    DOT             Department of Transportation   
..                       ...    ...                                      ...   
995  2022-03-20T21:31:56.000   NYPD          New York City Police Department   
996  2022-03-20T21:31:56.000   NYPD          New York City Police Department   
997  2022-03-20T21:31:42.000  DOHMH  Department of Health and Mental Hygiene   
998  2022-03-20T21:31:14.000   NYPD          New York City Police Department   
999  2022-03-20T21:31:12.000   NYPD          New York City Police Department   

            complaint_type                     descriptor  \
0         Blocked Driveway                      No Access   
1         Blocked Driveway                      No Access   
2          Noise - Vehicle                  Engine Idling   
3      Noise - Residential                Loud Television   
4    Street Sign - Missing                  Other/Unknown   
..                     ...                            ...   
995        Illegal Parking  Posted Parking Sign Violation   
996     Noise - Commercial               Loud Music/Party   
997     Food Establishment   Food Contains Foreign Object   
998    Noise - Residential                   Loud Talking   
999          Drug Activity                     Use Indoor   

                  location_type incident_zip         incident_address  \
0               Street/Sidewalk        11207       2869 FULTON STREET   
1               Street/Sidewalk        11207       2869 FULTON STREET   
2               Street/Sidewalk        11373          92-01 51 AVENUE   
3    Residential Building/House        10030     112 WEST  138 STREET   
4                        Street        10029    1501 LEXINGTON AVENUE   
..                          ...          ...                      ...   
995             Street/Sidewalk        11217         498 STATE STREET   
996         Club/Bar/Restaurant        10029     118 EAST  116 STREET   
997  Restaurant/Bar/Deli/Bakery        11429  217-95 HEMPSTEAD AVENUE   
998  Residential Building/House        10029         1405 PARK AVENUE   
999                       Other        11235        637 BANNER AVENUE   

       borough  
0     BROOKLYN  
1     BROOKLYN  
2       QUEENS  
3    MANHATTAN  
4    MANHATTAN  
..         ...  
995   BROOKLYN  
996  MANHATTAN  
997     QUEENS  
998  MANHATTAN  
999   BROOKLYN  

[1000 rows x 9 columns]

In [18]:
# Creating parsed table in calls.db
create_parsed_table = ''' CREATE TABLE calls(
                        id INTEGER PRIMARY KEY AUTOINCREMENT,
                        created_data TEXT,
                        agency TEXT, 
                        agency_name TEXT,
                        complaint_type TEXT,
                        descriptor TEXT,
                        location_type TEXT,
                        incident_zip TEXT,
                        incident_address TEXT,
                        borough TEXT
                        )'''

In [19]:
connector = sqlite3.connect('calls.db')
cursor = connector.cursor()
cursor.execute(create_parsed_table)
connector.close()

In [20]:
cleaned_data = data_extractor(get_raw())

In [21]:
def json_extractor(lst):
    return [tuple(x for x in [x for x in rows.values()]) for rows in lst]

In [22]:
holder = json_extractor(cleaned_data)

In [25]:
connector = sqlite3.connect('calls.db')
cursor = connector.cursor()
cursor.executemany("INSERT INTO calls (created_data,agency,agency_name,complaint_type,descriptor,location_type,incident_zip,incident_address,borough) VALUES (?,?,?,?,?,?,?,?,?)", holder)
connector.commit
connector.close()

ProgrammingError: Incorrect number of bindings supplied. The current statement uses 9, and there are 7 supplied.

In [ ]:
connector = sqlite3.connect('calls.db')
cursor = connector.cursor()
for row in connector.execute('SELECT * FROM calls WHERE borough=:borough', {'borough':'Queens'}):
    print(row)
connector.close()